In [1]:
import torch

from transformers import ElectraConfig, ElectraForMaskedLM, ElectraForPreTraining, load_tf_weights_in_electra
from tensorflow.keras.preprocessing import sequence
from transformers import BertTokenizer
import tensorflow as tf
from tensorflow import keras
from transformers import ElectraTokenizer, TFElectraModel, TFElectraForPreTraining
from transformers import ElectraConfig, ElectraForMaskedLM, ElectraForPreTraining, load_tf_weights_in_electra, TFElectraForPreTraining
from tensorflow.keras.preprocessing import sequence
from tensorflow.keras.utils import to_categorical
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report

import pandas as pd
from tqdm import tqdm

import argparse
import time
import gc
import numpy as np
import collections
import sys

In [2]:
tokenizer = BertTokenizer.from_pretrained('vocab.txt', do_lower_case=False)

Calling BertTokenizer.from_pretrained() with the path to a single file or url is deprecated


In [9]:
# 데이터 준비
df_IPCR = pd.read_csv('kipris_IPCR.csv')
df_CPC = pd.read_csv('kipris_CPC_rev.csv')

df_IPCR_CPC = pd.concat([df_IPCR, df_CPC])
del df_IPCR # 변수 삭제
print("df_IPCR 변수 삭제")
del df_CPC # 변수 삭제
print("df_CPC 변수 삭제")
gc.collect() # 메모리 삭제
print("gc.collect() 실행")

def return_code(IPCR, CPC): # 4자리 코드 반환
    if IPCR != IPCR:
        return CPC[2:6]
    elif CPC != CPC:
        return IPCR[2:6]

df_IPCR_CPC['Code'] = df_IPCR_CPC.apply(lambda x: return_code(x['MainIPCR'], x['MainCPC']), axis=1)
df_IPCR_CPC = df_IPCR_CPC.drop(['MainIPCR', 'FurtherIPCR', 'MainCPC', 'FurtherCPC'], axis=1)
df_IPCR_CPC = df_IPCR_CPC.reset_index(drop=True)

def tag_freq(df):
    freq_section = dict()

    try:
        for tag in df['Code']:
            temp_section = tag
            try:
                freq_section[temp_section] += 1
            except:
                freq_section[temp_section] = 1
    except:
        pass

    return freq_section

freq_code = tag_freq(df_IPCR_CPC)
sort_freq_code = sorted(freq_code.items(), key = lambda item: item[1], reverse=True)

freq_code = []
for n, (i, c) in enumerate(sort_freq_code):
    if c < 200:
        break
    print(n, '/', i, '/', c)
    freq_code.append(i)

df_IPCR_CPC = df_IPCR_CPC[df_IPCR_CPC['Code'].isin(freq_code)]
df_IPCR_CPC = df_IPCR_CPC.reset_index(drop=True)

del freq_code # 변수 삭제
del sort_freq_code # 변수 삭제
print("freq_code 변수 삭제")
gc.collect() # 메모리 삭제
print("gc.collect() 실행")

# #################### kisti label 만 사용 #########################
# if args.kisti_label == True:
#     kisti_label = pd.read_csv('korscibert/kisti-dataset/cpc_labelmap.tsv', sep='\t') # kisti label 준비
#     kisti_label.columns = ['Code']
#     df_IPCR_CPC = pd.merge(kisti_label, df_IPCR_CPC, on='Code', how='inner')
# #################### kisti label 만 사용 #########################

MAX_LENGTH = 256

#     col_list = ['제목', '청구항', '요약', '배경기술', '기술분야', '과제의 해결 수단', '발명의 상세한 설명']
col_list = ['제목', '청구항', '요약']
encode_train_data = []
y_data = pd.DataFrame()
train_text = []
for i in tqdm(range(2003, 2017+1)):
# for i in tqdm(range(2003, 2004)):
    file_name = 'L' + str(3) + '/pre_kipris_content_' + str(i) + '.csv'
    df_temp = pd.read_csv(file_name)
    df_temp = pd.merge(df_temp, df_IPCR_CPC, on='file_name', how='inner')
    df_temp = df_temp.drop(['file_name', '도면의 간단한 설명', 'i', 'j'], axis=1)
    df_temp = df_temp.fillna('') # nan값을 blank로 수정
    df_temp = df_temp.drop_duplicates() # 중복 삭제
    df_temp = df_temp.reset_index(drop=True)

    x_data = df_temp.iloc[:, :-1]
    y_data = pd.concat([y_data, df_temp.iloc[:, -1]])

    for i in tqdm(range(len(df_temp))):
#     for i in tqdm(range(3)):
        data = ''
        for j in range(len(col_list)):
            try:
                if x_data.loc[i][col_list[j]] != x_data.loc[i][col_list[j]]: # nan 값이라면 continue
                    continue
                if x_data.loc[i][col_list[j]][0] == '[' and x_data.loc[i][col_list[j]][-1] == ']': # 맨 앞에 '['와 맨 뒤에 ']'를 없애줌
                    x_data.loc[i][col_list[j]] = x_data.loc[i][col_list[j]][1:-1]
#                         print('[] 처리')
#                     temp = x_data.loc[i][col_list[j]].replace('u3000', ' ')
                temp = x_data.loc[i][col_list[j]].replace('u3000', ' ')[:80]
#                     if ' ' in temp and len(temp) > 256:
# #                     if ' ' in temp:
#                         temp = temp[:256]
#                         index = temp.rfind(' ')
#                         temp = temp[:index]
                data += temp + ' '
    #     data += '\n'
    #     print(data)
            except: # 컬럼 내용이 비어있으면 except 발생함 (= blank이면 except 발생)
#                 print("except 발생")
#                 print(i, col_list[j])
                continue
        data = data[:MAX_LENGTH]
        train_text.append(data)
        encode_train_data.append(tokenizer.encode(data, add_special_tokens = True, max_length=MAX_LENGTH, truncation=True))

y_data = y_data.iloc[:][0]
train_x = sequence.pad_sequences(encode_train_data, maxlen=MAX_LENGTH, value=0)
print("Original Text : ", x_data)
del x_data # 변수 삭제
print("x_data 변수 삭제")
del encode_train_data # 변수 삭제
print("encode_train_data 변수 삭제")
gc.collect() # 메모리 삭제
print("gc.collect() 실행")
#     print("Tokenizer Text : ", tokenizer.tokenize(x_data, add_special_tokens = True, max_length=MAX_LENGTH))
#     print("Encode Text : ", tokenizer.encode(x_data, add_special_tokens = True, max_length=MAX_LENGTH))

# category = set(y_data[:3])
category = set(y_data)
category_idx = dict()
for n, cate in enumerate(category):
    category_idx[cate] = n
idx_train_label = []
# for l in tqdm(y_data[:3]):
for l in tqdm(y_data):
    idx_train_label.append(category_idx[l])


train_y = to_categorical(idx_train_label)
print(train_x.shape, train_y.shape)
train_x_encode, test_x_encode, train_y_encode, test_y_encode = train_test_split(train_x, train_y, test_size=0.2, random_state=42)
train_x_text, test_x_text, train_y_text, test_y_text = train_test_split(train_text, y_data, test_size=0.2, random_state=42)
print('Train : {} / {}'.format(train_x.shape, train_y.shape))
print('Test : {} / {}'.format(test_x.shape, test_y.shape))

df_IPCR 변수 삭제
df_CPC 변수 삭제
gc.collect() 실행
0 / H01L / 160310
1 / G06F / 97090
2 / G06Q / 73634
3 / A61K / 60285
4 / H04N / 59759
5 / H04B / 48002
6 / H04L / 46004
7 / H01M / 41598
8 / H04W / 38677
9 / G02F / 36536
10 / G01N / 28308
11 / A23L / 26093
12 / C07D / 25344
13 / G02B / 24557
14 / A61B / 24519
15 / B65D / 22359
16 / B01D / 21320
17 / G09G / 19444
18 / B29C / 17613
19 / G11C / 17517
20 / G01R / 17330
21 / C12N / 17155
22 / H05B / 17124
23 / B63B / 16468
24 / C08L / 16215
25 / H05K / 15413
26 / B60R / 15152
27 / H01R / 14765
28 / F24F / 14360
29 / C02F / 14231
30 / G03F / 13443
31 / A01G / 12974
32 / A47J / 12906
33 / B32B / 12584
34 / H02J / 12535
35 / C23C / 12508
36 / A63B / 12493
37 / E02D / 12413
38 / C09K / 12293
39 / F21V / 12287
40 / A01K / 12284
41 / B62D / 12234
42 / B23K / 12108
43 / C07C / 11641
44 / C08G / 11471
45 / H01J / 11362
46 / G11B / 11295
47 / G06K / 11191
48 / H02K / 11082
49 / A61F / 11005
50 / C09D / 10678
51 / A45D / 10603
52 / G06T / 10567
53 / C07K / 

freq_code 변수 삭제
gc.collect() 실행


 13%|█▎        | 6270/48533 [00:14<01:37, 431.57it/s]


 26%|██▌       | 12535/48533 [00:28<01:22, 434.85it/s]


 39%|███▊      | 18783/48533 [00:43<01:07, 440.44it/s]


...

 83%|████████▎ | 31226/37436 [01:13<00:13, 443.65it/s]


100%|██████████| 15/15 [1:37:10<00:00, 388.69s/it]


Original Text :                                               제목  \
0                                       광고립 장치    
1      말풍선을 이용한 발신인의 발신메시지에 대한 답신메시지 수신 확인 시스템    
2            복합 무기 분체를 포함하는 화장료 조성물 및 이의 제조 방법    
3                      고정용 돌기부를 포함하는 계량기 단열 부재    
4                                  의자의 등판 틸팅장치    
...                                         ...   
37431                              천정 앙카 전용 드릴    
37432                     회수효율을 향상시킨 유가금속 회수장치    
37433                        상하수도 부분 보수장치 및 방법    
37434         레지스트 박리액 조성물 및 이를 이용한 레지스트의 박리방법    
37435                                롤 랙 앤 피니언    

                                               과제의 해결 수단  \
0      용어 광고립 장치는 어느 한 방향으로 입사된 광의 투과율이 그 반대 방향으로 입사된...   
1      말풍선 생성 및 스마트폰에서 말풍선 선택하는 방법들은 인터넷에 공개되어 있다소스를 ...   
2      상기 목적을 달성하기 위하여 본 발명의 일 실시예에 따른 복합 무기 분체를 포함하는...   
3      상기와 같은 목적을 달성하기 위해 본 고안의 일 측면은 일측에 개구부가 형성되고 타...   
4      상기 기술적 과제를 해결하기 위한 본 발명의 등판 틸팅장치는 좌판 하부를 가로지르는...   
...       

100%|██████████| 1909474/1909474 [00:01<00:00, 1684263.99it/s]


(1909474, 256) (1909474, 476)
Train : (1909474, 256) / (1909474, 476)
Test : (9707, 256) / (9707, 468)


In [14]:
# train_x_text와 train_x의 길이가 같은지 확인
# train_y_text와 train_y의 길이와 내용이 같은지 확인
len(train_x_encode)

1527579

In [20]:
(train_x_text)

['레이저 열 전사 장치 상기 장치를 사용하는 레이저 열 전사 방법 및 상기 장치를 사용하는 유기전계발광표시장치의 제조방법  억셉터 기판을 고정시키는 척 상기 척 상에 위치하고 상부 플레이트 및 하부 플레이트를 포함하는 바디부 및 상기 바디부에 연결된 가압수단을 구비하 본 발명은 레이저 열 전사 장치 상기 장치를 사용하는 레이저 열 전사 방법 및 상기 장치를 사용하는 유기전계발광표시장치의 제조방법에 관한 것으로 ',
 ' 구동회로  구동전압을 입력받아 일정한 전류량을 유지하는 구동전류를 제공하기 위한 정전류 레귤레이팅부 및 적어도 하나의 소자를 구비하고 상기 구동전류를 입력 본 발명은 입력되는 전압레벨이 변동하더라도 안정적으로 소자를 구동할 수 있는 구동회로를 제공한다 본 발명은 구동전압을 입력받아 일정한 전류량을  ',
 ' 히드록시테트라히드로퓨란의 효율적 제조방법  화학식 로 표시되는 히드록시테트라히드로퓨란을 제조하는 방법에 있어서 상기 방법이 화학식 로 표시되는 할로부탄디올을 물을 인위적으로 추가하지 아니 본 발명은 히드록시테트라히드로퓨란의 효율적 제조방법에 관한 것이다 보다 구체적으로는 본 발명은 할로부탄디올을 유기용매의 존재 하에 또는 용매를  ',
 '이반드로네이트 나트륨 다형태  형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 형태 이반드로네이트 나트륨의 결정 형태 및 그의 제조 방법이 제공된다  ',
 '아치 부재를 포함하는 치과교정용 기구 치과교정용 기구 로서아치 부재 몸체 및 상기 몸체에 연결되는 복수의 아치 부재 커플링 들을 포함하는 아치 부재 및 복수의 앵커들로서 앵커 커플링 치과교정용 기구 및 그러한 기구를 형성하는 방법의 다양한 실시예가 개시된다 하나 이상의 실시예에서 치과교정용 기구는 아치 부재 몸체 및 몸체에  ',
 '다목적 휴대용 메모리 드라이브  다목적 휴대용 메모리 드라이브에 있어서입출력되는 충전전원 또는 데이터의 전송을 제어하는 컨트

In [16]:
len(train_y_encode)

1527579

In [19]:
(train_y_text)
# len(train_text)

164855    H05B
88433     H05B
71173     C07D
35521     C07F
82136     A61C
          ... 
110110    E02D
59042     H01Q
83399     A61B
158768    G06Q
73425     B62D
Name: 0, Length: 1527579, dtype: object

In [24]:
df1 = pd.DataFrame({"text" : test_x_text, "code" : test_y_text})

In [26]:
df2 = pd.read_csv('top-3.csv')

In [72]:
df = pd.DataFrame({"text" : test_x_text, "True" : test_y_text, "top-1" : st, "top-2" : nd, "top-3" : th})
# df = pd.concat([df1, df2], axis=1)

In [74]:
pd.set_option('display.max_colwidth', None)


In [79]:
df[df["True"]=='F21K']

text  \
38          백색 발광장치 및 그의 제조방법   또는 광원 시트 및 상기 광원 시트에 의해 여기될 수 있고 노출면에 개 이상의 나노닷 을 분산된 형태로 포함하는 형광체 시트를 적층된 형태로  본 발명은 백색 발광장치 및 그의 제조방법에 관한 것으로 또는 광원 시트 및 상기 광원 시트에 의해 여기될 수 있고 노출면에 개 이상의 나노닷     
95      광학 소자의 제조 및 이를 통합한 모듈  웨이퍼스케일 스페이서광학 구조를 제조하는 방법으로서광학 소자 복제 부분들과 스페이서 복제 부분들을 갖는 복제 도구를 제공하는 단계제 재료의 복제 웨이퍼스케일 스페이서광학 구조를 제조하는 것은 단일의 복제 도구를 사용하여 직접적으로 광학 웨이퍼또는 다른 웨이퍼 위에 광학적 복제 소자들과 스    
1288      발광소자 및 이를 포함하는 발광벌브  비도전성 투명기판상기 비도전성 투명기판의 상면에 실장되고 상기 비도전성 투명기판을 향해 연장된 입력단과 출력단을 포함하는 하나 이상의 발광다이오 필라멘트 타입 발광소자가 개시된다 이 발광소자는 비도전성 투명기판 상기 비도전성 투명기판의 상면에 어레이되고 상기 비도전성 투명기판을 향해 연장    
4639                레이저 조명 장치  레이저광을 방출하는 레이저 다이오드상기 레이저광이 입사되고 입사된 상기 레이저광의 일부에 의해 여기되어 방출되는 상기 레이저광과 상이한 파장의  본 발명은 레이저 조명 장치에 관한 것으로서 보다 상세하게는 레이저 다이오드를 이용하는 레이저 조명 장치에 관한 것이다본 발명의 일실시예에 따른    
7397         유브이 경화장치용 엘이디 모듈  제 플레이트상기 제 플레이트의 측면에 수직방향으로 연결되며 위치이동 가능한 제 플레이트상기 제 플레이트와 제 플레이트 상에 서로 연결되게 구비되 본 발명은 각종 평판표시패널의 합착에 사용되는 레진을 경화시키는 엘이디 램프가 열 이상으로 배열됨과 동시에 광이 교차되는 지점에 반사판과 보강     
...                                                                                                                                                                                           ...   
358668                  조명 장치  내주면과 외주면을 갖는 바디상기 바디 상에 배치되며 상기 바디의 가장자리를 따라 배치된 회로 기판 및 상기 회로 기판에 실장된 복수 개의 광원을 실시 예는 조명 장치에 관한 것으로 내주면과 외주면을 갖는 바디 상기 바디 상에 배치되며 상기 바디의 가장자리를 따라 배치된 회로 기판 및 상기    
372838             에지형 면조명 장치  에지형 면조명 장치에 있어서 제 프레임과 상기 제 프레임과 소정의 각을 이루도록 배치되는 제 프레임을 포함하는 프레임 부재로서 상기 제 프레임과 본 고안은 에지형 면조명 장치에 관한 것이다 상기 에지형 면조명 장치는 제 프레임과 상기 제 프레임과 소정의 각을 이루도록 배치되는 제 프레임을    
378618                    조명등  실내 또는 실외의 천장에 설치되어 빛을 조사하기 위한 조명등에 있어서천장에 조명등 설치시 천장에 조명등을 고정하기 위해 형성되는 메인프레임과 상 본 발명은 조명등에 관한 것으로 보다 상세하게는 적어도 하나 이상의 색을 갖는 메인광원을 통해 사용자의 선택에 따라 빛을 조사하도록 하며 보조광    
379353  스트립 조명 및 이를 응용한 조명 장치  스트립 조명으로서광 투과성을 갖는 가요성 베이스플레이트인 투명 베이스플레이트각각이 적어도 하나의 도전막을 통해 상기 투명 베이스플레이트에 고정적 본 발명의 스트립 조명은 투명 베이스플레이트 상에 장착된 적어도 하나의 발광 다이오드로 구성된다 또한 보호층이 투명 베이스플레이트 및 각각의 발    
381708                 투광 등기구  내측에 하부가 개방된 수납공간부를 갖는 본체와 상기 본체에 형성된 수납공간부 내에 배치되어 전원 공급장치로부터 공급되는 전류를 인가받아 점등하는 본 발명은 기판의 저면에 배치된 각 발광 다이오드에서 발산되는 빛의 개별적인 확산을 도모하여 향상된 조도를 확보하고 빛의 발산과정에서 생성된 열    

        True top-1 top-2    top-3  
38      F21K  H01L  H05B     F21S  
95      F21K  G02B  H01L     B81C  
1288    F21K  H01L  F21S     H05B  
4639    F21K  F21V  H01S     F21K  
7397    F21K  F21S  H01L     F21V  
...      ...   ...   ...      ...  
358668  F21K  F21V  F21K     F21S  
372838  F21K  F21V  F21K     F21S  
378618  F21K  F21V  F21S     H05B  
379353  F21K  F21V  F21K     F21S  
381708  F21K  F21V  F21K     F21S  

[114 rows x 5 columns]